**В данном файле представлена генерация рекомендаций при помощи SVD**

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


Импорт необходимых библиотек

In [2]:
import pandas as pd
import numpy as np
import zipfile
import os
import gc
import scipy
from collections import defaultdict
from google.colab import drive
from tqdm import tqdm

drive.mount('/content/drive')

print("loading data ...")
#hack = pd.read_csv('/content/drive/MyDrive/Цифровой прорыв/small_player_starts_train.csv')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
loading data ...


Чтение созданного датасета (его создание показано в файле merge_big_data.ipynb)

In [3]:
hack = pd.read_csv('/content/drive/MyDrive/Цифровой прорыв/final_user_video_reaction_meta.csv')

<ipython-input-3-a814bd1eeae7>:1: DtypeWarning: Columns (9) have mixed types. Specify dtype option on import or set low_memory=False.
  hack = pd.read_csv('/content/drive/MyDrive/Цифровой прорыв/final_user_video_reaction_meta.csv')


In [4]:
hack.head(10)

Unnamed: 0        user_id        item_id                 date_watch  \
0           0  user_10000000  video_1487101  2023-08-21 20:25:47+03:00   
1           1  user_10000000   video_222807  2023-08-21 19:06:33+03:00   
2           2  user_10000033  video_1761620  2023-08-21 07:02:56+03:00   
3           3  user_10000087  video_1106848  2023-08-21 03:55:46+03:00   
4           4  user_10000087   video_633280  2023-08-21 04:04:26+03:00   
5           5  user_10000092  video_2137593  2023-08-21 17:40:31+03:00   
6           6  user_10000099  video_2224179  2023-08-21 09:25:44+03:00   
7           7  user_10000099    video_30396  2023-08-21 09:29:18+03:00   
8           8  user_10000099   video_856096  2023-08-21 09:22:38+03:00   
9           9  user_10000115   video_283933  2023-08-21 12:19:19+03:00   

   watch_time  is_autorized              date_reaction pos_emo  is_v_top  \
0        2310             0                        NaN     NaN       NaN   
1        4611             0                        NaN     NaN       NaN   
2         196             0                        NaN     NaN       NaN   
3         490             0                        NaN     NaN       NaN   
4           1             0                        NaN     NaN       NaN   
5          52             0                        NaN     NaN       NaN   
6         171             1                        NaN     NaN       NaN   
7         102             1  2023-08-21 06:29:26+03:00    Like       0.0   
8         172             1                        NaN     NaN       NaN   
9        2493             0                        NaN     NaN       NaN   

  neg_emo  ...                                  video_description  \
0     NaN  ...  Премьера! В третьем сезоне экстремально-приклю...   
1     NaN  ...  «Четыре свадьбы» отправляются в Турцию! Невест...   
2     NaN  ...  В прямом эфире Соловьёв LIVE – новости и размы...   
3     NaN  ...  ЙОУ БЕЗРАБОТНЫЕ, это полное прохождение НОВОГО...   
4     NaN  ...  Atomic Heart - «Инстинкт Истребления»  Прохожд...   
5     NaN  ...  Всем привет! Приветствую вас на своем канале "...   
6     NaN  ...                                                NaN   
7     NaN  ...  Как приготовить рваную говядину на углях. Реце...   
8     NaN  ...                                                NaN   
9     NaN  ...  Премьера! «Выжить в Дубае» – новое масштабное ...   

  category_title                 publicated   duration channel_sub tv_sub  \
0   Телепередачи  2022-12-05 11:00:20+03:00   5377.480       75496      0   
1   Телепередачи  2023-08-10 21:19:06+03:00   6919.000       16723      0   
2   Телепередачи  2022-10-14 12:06:53+03:00  70972.000      343030      0   
3      Видеоигры  2023-08-17 13:57:07+03:00   1059.917       19764      0   
4      Видеоигры  2023-08-14 10:00:20+03:00   3286.529          59      0   
5      Эзотерика  2023-08-12 09:16:18+03:00    283.240       28896      0   
6      Кулинария  2023-08-16 19:02:11+03:00    179.240           1      0   
7      Кулинария  2023-08-17 13:10:00+03:00    922.854        1410      0   
8      Кулинария  2023-08-21 09:21:58+03:00    176.360           1      0   
9   Телепередачи  2023-08-20 21:00:23+03:00   5616.280       75496      0   

  ctr.CTR_10days_21_07  ctr.CTR_10days_01_08  ctr.CTR_10days_10_08  \
0             0.294598              0.260142              0.237338   
1             0.000000              0.000000              0.025105   
2             0.000000              0.000000              0.000000   
3             0.000000              0.000000              0.000000   
4             0.000000              0.000000              0.000000   
5             0.000000              0.000000              0.000000   
6             0.000000              0.000000              0.000000   
7             0.000000              0.000000              0.000000   
8             0.000000              0.000000              0.000000   
9             0.000000              0.00000

In [5]:
POS_EMO_COEF = 1.2
V_TOP_COEF = 1.3
MAX_VALUE = 2.7

hack['is_v_top'] = np.where(hack['is_v_top'] == 1, V_TOP_COEF, 1)
hack['pos_emo'] = np.where(hack['pos_emo'].isna(), 1, POS_EMO_COEF)
hack['val'] = ((hack['watch_time']/hack['duration']) * hack['is_v_top'] * hack['pos_emo'] + hack['ctr.CTR_10days_21_08'])/MAX_VALUE
hack_val = hack[['user_id','item_id','val','category_title']].fillna(0)
hack_val.head()

user_id        item_id       val category_title
0  user_10000000  video_1487101  0.252770   Телепередачи
1  user_10000000   video_222807  0.261531   Телепередачи
2  user_10000033  video_1761620  0.001023   Телепередачи
3  user_10000087  video_1106848  0.175047      Видеоигры
4  user_10000087   video_633280  0.004404      Видеоигры

##**Определение схожих категорий**





Пример получения категорий, которые были бы интересны пользователю. Определяется основная категория для каждого пользователя (та, из которой просмотрено больше всего видео), к ней добавляются еще 3 категории, которые обычно смотрят вместе с данной категорией.

In [12]:
def calc_pairs(train):
    print("Get sessions")
    count = train.groupby(['category_title']).size().rename('count_source').reset_index()[
        ['category_title', 'count_source']]
    dt = train.groupby(['user_id'])['category_title'].agg(list).rename('pair').reset_index()
    df = train[['user_id', 'category_title']].merge(dt, on=['user_id'], how='left')

    del dt
    gc.collect()

    # Explode the rows vs list of articles
    print("Explode the rows vs list of articles")
    df = df[['category_title', 'pair']].explode(column='pair')
    gc.collect()

    print("Discard duplicates")
    df = df.loc[df['category_title'] != df['pair']].reset_index(drop=True)

    print("Count how many times each pair combination happens")
    df = df.groupby(['category_title', 'pair']).size().rename('count').reset_index()

    print("join with frecuency of source item")
    df = df.merge(count, on=['category_title'], how='left')
    count = count.rename({'count_source': 'count_target', 'category_title': 'pair'}, axis=1)
    df = df.merge(count, on=['pair'], how='left')

    df['score'] = df.apply(lambda l: l['count'] / (l['count_source']*l['count_target']), axis=1)
    df.sort_values(by=['score'], ascending=False, inplace=True)
    gc.collect()
    return df

In [13]:
rules = calc_pairs(hack[['user_id', 'category_title']])

Get sessions
Explode the rows vs list of articles
Discard duplicates
Count how many times each pair combination happens
join with frecuency of source item


In [14]:
predictions = rules[rules.category_title=='Аудиокниги'].pair.to_list()[:3]
prediction_names = [hack[hack.category_title == pred]['category_title'].values[0] for pred in predictions]
prediction_names

['Природа', 'Детям', 'Кулинария']

# **SVD v1**

In [15]:
from scipy.sparse import csr_matrix

def create_matrix(hack_val, category, N, user_mapper):

    V = len(hack_val['item_id'][hack_val['category_title'] == category].unique())

    # Map Ids to indices
    video_mapper = dict(zip(np.unique(hack_val["item_id"][hack_val['category_title'] == category]), list(range(V))))

    user_index = [user_mapper[i] for i in hack_val['user_id'][hack_val['category_title'] == category]]
    video_index = [video_mapper[i] for i in hack_val['item_id'][hack_val['category_title'] == category]]

    X = csr_matrix((hack_val["val"][hack_val['category_title'] == category], (video_index, user_index)), shape=(V, N))

    return X, video_mapper


In [16]:
categories = list(categories)
dict_by_category = {}
N = len(hack_val['user_id'].unique())
user_mapper = dict(zip(np.unique(hack_val["user_id"]), list(range(N))))

for c in tqdm(categories):
    dict_by_category[c] = {}
    X, video_mapper = create_matrix(hack_val, c, N, user_mapper)
    dict_by_category[c]['matrix'] = X
    dict_by_category[c]['video_mapper'] = video_mapper

100%|██████████| 45/45 [00:36<00:00,  1.23it/s]


In [17]:
def MSE(R, U, V, ind_users, ind_videos,new_N):
    mse = 0
    for ind in range(new_N):
        i = ind_users[ind]
        j = ind_videos[ind]
        mse += ( R[i,j] - np.dot(U[i,:], V[:,j]) )**2 / N
    return mse

In [18]:
def SVD(ind_users, ind_videos, R, d, step, n_iters,new_N):

    # инициализация матриц разложения
    P = np.random.rand(R.shape[0], d)
    Q = np.random.rand(d, R.shape[1])

    start_mse = MSE(R, P, Q, ind_users, ind_videos,new_N)

    # Стохастический градиентный спуск
    for n in tqdm(range(n_iters)):
        ind = np.random.randint(0, new_N)
        i = ind_users[ind]
        j = ind_videos[ind]

        for k in range(0, d):
            P[i, k] = P[i, k] + step * (R[i,j] - P[i, :] @ Q[:, j]) * Q[k, j]
            Q[k, j] = Q[k, j] + step * (R[i,j] - P[i, :] @ Q[:, j]) * P[i, k]

        mse = MSE(R, P, Q, ind_users, ind_videos,new_N)
    return P, Q, start_mse, mse


In [19]:
df_sample = pd.read_csv('/content/drive/MyDrive/Цифровой прорыв/sample_submission.csv')

In [20]:
user_mapper = dict(zip(np.unique(df_sample["user_id"]), list(range(N))))

Основная функция для получения рекомендаций

In [21]:
ind_users = list(user_mapper.values())
# Функция для получения рекомендации для одного юзера по одной категории
def make_matrix_by_category_for_user(user_id, category_name):
  ind_videos = list(dict_by_category[category_name]['video_mapper'].values())
  user_id = user_mapper[user_id]
  #print(len(ind_users),len(ind_videos))
  new_N = len(dict_by_category[category_name]['video_mapper'].values())
  new_N = 1
  R = dict_by_category[category_name]['matrix']
  R = R.T
  MSE(R, np.random.rand(R.shape[0], 3), np.random.rand(3, R.shape[1]), [user_id], ind_videos,new_N)
  P, Q, start_mse, mse = SVD([user_id], ind_videos, R, 3, 0.01, 100, new_N)
  #return P, Q, start_mse, mse
  R_pred = np.zeros((1, R.shape[1]))
  # Вот так надо, но это 1,5 часа (И это только для одной категории, а для каждой это блять сколько будет???)((Хотя ладно, это обучение))
  n_users = len(user_mapper.values())
  # А это только для первых 10 пользователей
  n_users = 1
  n_videos = len(dict_by_category[category_name]['video_mapper'].values())
  for i in tqdm(range(n_users)):
      for j in range(n_videos):
          R_pred[i][j] = round(P[i,:] @ Q[:,j], 2)
  users = list(user_mapper.keys())
  videos = list(dict_by_category[category_name]['video_mapper'].keys())
  result = pd.DataFrame(R_pred, [user_id], videos)
  return result

In [22]:
# Пример использования функции
res_user_10589824 = make_matrix_by_category_for_user('user_10589824', 'Детям')

100%|██████████| 1/1 [00:00<00:00, 14.27it/s]


Пример получаемых рекомендаций (чем больше оценка, тем больше видео будет интересно юзеру)

In [23]:
res_user_10589824

video_100059  video_1000645  video_100102  video_1001289  video_1001315  \
1337          0.49           0.43          0.23           0.67           1.35   

      video_1001527  video_1001956  video_1002075  video_1002087  \
1337           0.82           1.29           0.43           1.12   

      video_1002515  ...  video_997770  video_997866  video_997984  \
1337           0.46  ...          0.79          1.11          0.98   

      video_998199  video_998492  video_998497  video_99850  video_998812  \
1337           0.6          1.36          1.02         0.65          0.91   

      video_999296  video_999670  
1337          1.33          0.33  

[1 rows x 9723 columns]

In [24]:
# Получение предпочитаемой категории для юзера
prime_cats = hack.groupby(['user_id','category_title']).agg({'Unnamed: 0': 'count'}).reset_index().sort_values(by='Unnamed: 0',ascending=False).drop_duplicates(subset=['user_id'], keep='first')

In [25]:
sample_users = set(user_mapper.keys())
users_with_history = set(prime_cats['user_id'].unique())

In [26]:
df_sample_submission = pd.DataFrame(list(user_mapper.keys()), columns=['user_id'])
df_sample_submission['recs'] = np.empty((len(df_sample_submission), 0)).tolist()
df_sample_submission['coefs'] = np.empty((len(df_sample_submission), 0)).tolist()

Генерация рекомендаций для юзеров

In [28]:
for i,row in tqdm(df_sample_submission.iterrows()):
  user_result = []
  user_coefs = []
  if row['user_id'] not in users_with_history:
    continue
  prime_cat = prime_cats[prime_cats['user_id'] == row['user_id']]['category_title'].values[0]
  # Берем три категории, которые могут быть интересны юзеру
  print(prime_cat)
  predictions = rules[rules.category_title==prime_cat].pair.to_list()[:3]
  prediction_names = [hack[hack.category_title == pred]['category_title'].values[0] for pred in predictions]
  prime_recs = make_matrix_by_category_for_user(row['user_id'], prime_cat)
  cols_for_max = list(prime_recs.T.reset_index())[1]
  videos = prime_recs.T.reset_index().nlargest(70, columns=cols_for_max)['index'].tolist()
  coefs = prime_recs.T.reset_index().nlargest(70, columns=cols_for_max)[cols_for_max].tolist()
  row['recs'].extend(videos)
  row['coefs'].extend(coefs)
  for pred in prediction_names:
    prime_recs = make_matrix_by_category_for_user(row['user_id'], pred)
    cols_for_max = list(prime_recs.T.reset_index())[1]
    videos = prime_recs.T.reset_index().nlargest(10, columns=cols_for_max)['index'].tolist()
    coefs = prime_recs.T.reset_index().nlargest(10, columns=cols_for_max)[cols_for_max].tolist()
    row['recs'].extend(videos)
    row['coefs'].extend(coefs)

0it [00:00, ?it/s]

Телепередачи



100%|██████████| 100/100 [00:00<00:00, 3432.36it/s]

100%|██████████| 1/1 [00:00<00:00,  6.65it/s]

100%|██████████| 100/100 [00:00<00:00, 5353.97it/s]

100%|██████████| 1/1 [00:00<00:00, 12.30it/s]

100%|██████████| 100/100 [00:00<00:00, 4986.04it/s]

100%|██████████| 1/1 [00:00<00:00, 557.01it/s]

100%|██████████| 100/100 [00:00<00:00, 3386.49it/s]

100%|██████████| 1/1 [00:00<00:00, 32.32it/s]
1it [00:01,  1.36s/it]

Сериалы



100%|██████████| 100/100 [00:00<00:00, 4831.81it/s]

100%|██████████| 1/1 [00:00<00:00,  8.84it/s]

100%|██████████| 100/100 [00:00<00:00, 4633.21it/s]

100%|██████████| 1/1 [00:00<00:00, 4219.62it/s]

100%|██████████| 100/100 [00:00<00:00, 3106.62it/s]

100%|██████████| 1/1 [00:00<00:00, 21.32it/s]

100%|██████████| 100/100 [00:00<00:00, 3192.09it/s]

100%|██████████| 1/1 [00:00<00:00, 74.47it/s]
2it [00:02,  1.29s/it]

...


100%|██████████| 100/100 [00:00<00:00, 3044.34it/s]

100%|██████████| 1/1 [00:00<00:00,  2.98it/s]

100%|██████████| 100/100 [00:00<00:00, 2249.15it/s]

100%|██████████| 1/1 [00:00<00:00,  6.32it/s]

100%|██████████| 100/100 [00:00<00:00, 2741.89it/s]

100%|██████████| 1/1 [00:00<00:00, 4481.09it/s]

100%|██████████| 100/100 [00:00<00:00, 3010.60it/s]

100%|██████████| 1/1 [00:00<00:00, 16.59it/s]
6604it [2:16:20,  1.35s/it]

Телепередачи



100%|██████████| 100/100 [00:00<00:00, 2025.49it/s]

100%|██████████| 1/1 [00:00<00:00,  2.94it/s]

100%|██████████| 100/100 [00:00<00:00, 2345.79it/s]

100%|██████████| 1/1 [00:00<00:00,  5.24it/s]

100%|██████████| 100/100 [00:00<00:00, 2561.77it/s]

100%|██████████| 1/1 [00:00<00:00, 4215.38it/s]

100%|██████████| 100/100 [00:00<00:00, 2491.60it/s]

100%|██████████| 1/1 [00:00<00:00, 16.47it/s]
6605it [2:16:23,  1.60s/it]

Телепередачи



100%|██████████| 100/100 [00:00<00:00, 2432.41it/s]

100%|██████████| 1/1 [00:00<00:00,  3.04it/s]

100%|██████████| 100/100 [00:00<00:00, 2549.67it/s]

100%|██████████| 1/1 [00:00<00:00,  7.14it/s]



Выгрузка результатов

In [29]:
df_sample_submission.to_csv('/content/drive/My Drive/Цифровой прорыв/our_svd_submission.csv',index=False)